In [2]:
import os
import cv2
import numpy as np
from sklearn.model_selection import train_test_split
from tensorflow.keras.applications import ResNet50
from tensorflow.keras.layers import Dense, Flatten, Dropout
from keras.layers import Conv2D, MaxPooling2D, Flatten, Dense
from tensorflow.keras.models import Model
from tensorflow.keras.optimizers import Adam
from tensorflow.keras.utils import to_categorical
from keras.models import Sequential
from flask import Flask, request, jsonify
from keras.preprocessing import image
from keras.models import load_model
from keras.models import save_model

In [3]:
import numpy as np 
import pandas as pd 



import os
for dirname, _, filenames in os.walk('/kaggle/input/medical-image-dataset-brain-tumor-detection/TumorDetectionYolov8/OD8/Brain Tumor Detection'):
    for filename in filenames:
        print(os.path.join(dirname, filename))


/kaggle/input/medical-image-dataset-brain-tumor-detection/TumorDetectionYolov8/OD8/Brain Tumor Detection/README.txt
/kaggle/input/medical-image-dataset-brain-tumor-detection/TumorDetectionYolov8/OD8/Brain Tumor Detection/data.yaml
/kaggle/input/medical-image-dataset-brain-tumor-detection/TumorDetectionYolov8/OD8/Brain Tumor Detection/valid/labels/volume_114_slice_79_jpg.rf.fe0c58a00e797af3cbf938f1002b7e2e.txt
/kaggle/input/medical-image-dataset-brain-tumor-detection/TumorDetectionYolov8/OD8/Brain Tumor Detection/valid/labels/volume_24_slice_39_jpg.rf.fd1811e29c9532d9ddff3887d33205c4.txt
/kaggle/input/medical-image-dataset-brain-tumor-detection/TumorDetectionYolov8/OD8/Brain Tumor Detection/valid/labels/volume_196_slice_74_jpg.rf.8740e0d17ebc28a608a07baff30a2c80.txt
/kaggle/input/medical-image-dataset-brain-tumor-detection/TumorDetectionYolov8/OD8/Brain Tumor Detection/valid/labels/volume_125_slice_74_jpg.rf.8bdbc24905a8e3ea3642bd813cfd8404.txt
/kaggle/input/medical-image-dataset-brain-

In [4]:
def load_data(data_dir):
    images = []
    labels = []

    for filename in os.listdir(os.path.join(data_dir, "images")):
        if filename.endswith('.jpg'):
            img_path = os.path.join(data_dir, "images", filename)
            label_path = os.path.join(data_dir, "labels", filename.replace('.jpg', '.txt'))

            print(f"Processing {filename}...")  # Print filename for debugging

            if os.path.isfile(label_path):
                with open(label_path, 'r') as label_file:
                    line = label_file.readline().strip()

                    if not line:
                        print(f"Empty line in file: {label_path}")
                        continue

                    try:
                        label = int(line.split()[0])
                        labels.append(label)
                    except (ValueError, IndexError) as e:
                        print(f"Error processing line in file {label_path}: {line}")
                        print(f"Error details: {e}")

                # Resize the image to the expected input shape (224, 224)
                img = cv2.imread(img_path)
                img = cv2.resize(img, (224, 224))
                images.append(img)

    return np.array(images), np.array(labels)


# Specify your dataset directory
dataset_dir = '/kaggle/input/medical-image-dataset-brain-tumor-detection/TumorDetectionYolov8/OD8/Brain Tumor Detection/train'


# Load the data
images, labels = load_data(dataset_dir)

Processing volume_86_slice_51_jpg.rf.a60dcff23274dcebaf3786afa7002869.jpg...
Processing volume_243_slice_37_jpg.rf.ffb8d8d66a305b54b38d23f0f083b94f.jpg...
Processing volume_269_slice_98_jpg.rf.c56cadbb8718754ff46170a2a952288f.jpg...
Processing volume_13_slice_75_jpg.rf.b310f7fd7b6371793e9b9d30b1522cae.jpg...
Processing volume_240_slice_83_jpg.rf.b11c986d3da4ab52273b92f13b48c3b1.jpg...
Processing volume_259_slice_72_jpg.rf.3abdb50f25f6d564c11941442829f491.jpg...
Processing volume_74_slice_127_jpg.rf.ed4377ede2c7fd092793d5ca60a0999e.jpg...
Processing volume_355_slice_128_jpg.rf.47e9791ce92b48faf1f627042bd41e4f.jpg...
Processing volume_107_slice_110_jpg.rf.6ddc16786cad0abf2f847cbfcee2c3f8.jpg...
Processing volume_124_slice_81_jpg.rf.553bcf7110ae8a84f96a6012d35c0b74.jpg...
Processing volume_307_slice_106_jpg.rf.f474c4547a374803b8d312eaee6609ca.jpg...
Processing volume_233_slice_80_jpg.rf.0327990cc2db94dd9f84c47a137acf5e.jpg...
Processing volume_284_slice_62_jpg.rf.dacc6c3bb8a7ba8785b5aa6f7

In [5]:
X_train, X_test, y_train, y_test = train_test_split(images, labels, test_size=0.2, random_state=42)

In [6]:

min_label = np.min(y_train)
y_train = y_train - min_label
y_test = y_test - min_label


num_classes = len(np.unique(y_train))


y_train_categorical = to_categorical(y_train, num_classes=num_classes)
y_test_categorical = to_categorical(y_test, num_classes=num_classes)
print(num_classes)

3


**RESNET50**

In [7]:

base_model = ResNet50(weights='imagenet', include_top=False, input_shape=(224, 224, 3))


x = base_model.output
x = Flatten()(x)
x = Dense(512, activation='relu')(x)
x = Dropout(0.5)(x)
output = Dense(num_classes, activation='softmax')(x)


model = Model(inputs=base_model.input, outputs=output)


model.compile(optimizer=Adam(), loss='categorical_crossentropy', metrics=['accuracy'])


model.fit(X_train, y_train_categorical, epochs=10, batch_size=32, validation_data=(X_test, y_test_categorical))


accuracy = model.evaluate(X_test, y_test_categorical)[1]
print(f'Test Accuracy: {accuracy}')

Epoch 1/10
172/172 [==============================] - 74s 200ms/step - loss: 4.3121 - accuracy: 0.6109 - val_loss: 10.0195 - val_accuracy: 0.6448
Epoch 2/10
172/172 [==============================] - 31s 183ms/step - loss: 0.6739 - accuracy: 0.6538 - val_loss: 0.9753 - val_accuracy: 0.6827
Epoch 3/10
172/172 [==============================] - 31s 183ms/step - loss: 0.6114 - accuracy: 0.7071 - val_loss: 0.5985 - val_accuracy: 0.7017
Epoch 4/10
172/172 [==============================] - 31s 183ms/step - loss: 0.5474 - accuracy: 0.7442 - val_loss: 0.5246 - val_accuracy: 0.7535
Epoch 5/10
172/172 [==============================] - 31s 183ms/step - loss: 0.4759 - accuracy: 0.7816 - val_loss: 0.4856 - val_accuracy: 0.7819
Epoch 6/10
172/172 [==============================] - 31s 183ms/step - loss: 0.4109 - accuracy: 0.8197 - val_loss: 0.4928 - val_accuracy: 0.7775
Epoch 7/10
172/172 [==============================] - 31s 183ms/step - loss: 0.3128 - accuracy: 0.8739 - val_loss: 0.6282 - val_a

**CNN**

In [8]:

X_train = X_train / 255.0
X_test = X_test / 255.0


min_label = np.min(y_train)
y_train = y_train - min_label
y_test = y_test - min_label


num_classes = len(np.unique(y_train))


y_train_categorical = to_categorical(y_train, num_classes=num_classes)
y_test_categorical = to_categorical(y_test, num_classes=num_classes)


X_train, X_val, y_train_encoded, y_val_encoded = train_test_split(X_train, y_train_categorical, test_size=0.2, random_state=42)


model = Sequential()
model.add(Conv2D(32, (3, 3), activation='relu', input_shape=(224, 224, 3)))
model.add(MaxPooling2D((2, 2)))
model.add(Conv2D(64, (3, 3), activation='relu'))
model.add(MaxPooling2D((2, 2)))
model.add(Conv2D(128, (3, 3), activation='relu'))
model.add(MaxPooling2D((2, 2)))
model.add(Flatten())
model.add(Dense(128, activation='relu'))
model.add(Dense(num_classes, activation='softmax'))


model.compile(optimizer='adam', loss='categorical_crossentropy', metrics=['accuracy'])


model.fit(X_train, y_train_encoded, epochs=10, batch_size=32, validation_data=(X_val, y_val_encoded))

# Evaluate the model on the test set
test_loss, test_accuracy = model.evaluate(X_test, y_test_categorical)
print(f'Test Loss: {test_loss}, Test Accuracy: {test_accuracy}')

Epoch 1/10
137/137 [==============================] - 9s 48ms/step - loss: 0.6499 - accuracy: 0.6585 - val_loss: 1.1606 - val_accuracy: 0.6515
Epoch 2/10
137/137 [==============================] - 4s 32ms/step - loss: 0.5612 - accuracy: 0.7167 - val_loss: 0.9725 - val_accuracy: 0.7181
Epoch 3/10
137/137 [==============================] - 4s 32ms/step - loss: 0.4726 - accuracy: 0.7719 - val_loss: 1.0366 - val_accuracy: 0.7518
Epoch 4/10
137/137 [==============================] - 4s 32ms/step - loss: 0.3372 - accuracy: 0.8488 - val_loss: 1.6371 - val_accuracy: 0.7162
Epoch 5/10
137/137 [==============================] - 4s 33ms/step - loss: 0.2063 - accuracy: 0.9202 - val_loss: 1.9102 - val_accuracy: 0.7591
Epoch 6/10
137/137 [==============================] - 4s 32ms/step - loss: 0.1262 - accuracy: 0.9526 - val_loss: 2.4917 - val_accuracy: 0.7427
Epoch 7/10
137/137 [==============================] - 4s 32ms/step - loss: 0.0758 - accuracy: 0.9745 - val_loss: 2.7829 - val_accuracy: 0.7692

In [9]:
print(f'Shape of X_train: {X_train.shape}')
print(f'Shape of y_train_categorical: {y_train_categorical.shape}')


Shape of X_train: (4384, 224, 224, 3)
Shape of y_train_categorical: (5480, 3)


**CNN+LSTM**

In [19]:
from keras.layers import LSTM, Reshape


X_test = X_test / 255.0

min_label = np.min(y_train)
X_train, y_train = X_train[:min(len(X_train), len(y_train))], y_train[:min(len(X_train), len(y_train))]
y_test = y_test - min_label

num_classes = len(np.unique(y_train))
y_train_categorical = to_categorical(y_train, num_classes=num_classes)
y_test_categorical = to_categorical(y_test, num_classes=num_classes)

X_train, X_val, y_train_encoded, y_val_encoded = train_test_split(X_train, y_train_categorical, test_size=0.2, random_state=42)
model = Sequential()


model.add(Conv2D(32, (3, 3), activation='relu', input_shape=(224, 224, 3)))
model.add(MaxPooling2D((2, 2)))
model.add(Conv2D(64, (3, 3), activation='relu'))
model.add(MaxPooling2D((2, 2)))
model.add(Conv2D(128, (3, 3), activation='relu'))
model.add(MaxPooling2D((2, 2)))


model.add(Flatten())
model.add(Reshape((1, -1))) 


model.add(LSTM(64, activation='relu'))


model.add(Dense(128, activation='relu'))
model.add(Dense(num_classes, activation='softmax'))


model.compile(optimizer='adam', loss='categorical_crossentropy', metrics=['accuracy'])


model.fit(X_train, y_train_encoded, epochs=20, batch_size=64, validation_data=(X_val, y_val_encoded))





Epoch 1/20
10/10 [==============================] - 6s 148ms/step - loss: 0.8003 - accuracy: 0.5588 - val_loss: 0.7568 - val_accuracy: 0.6803
Epoch 2/20
10/10 [==============================] - 1s 64ms/step - loss: 0.7161 - accuracy: 0.5554 - val_loss: 0.8699 - val_accuracy: 0.5578
Epoch 3/20
10/10 [==============================] - 1s 67ms/step - loss: 0.6542 - accuracy: 0.6422 - val_loss: 0.8017 - val_accuracy: 0.4762
Epoch 4/20
10/10 [==============================] - 1s 67ms/step - loss: 0.6693 - accuracy: 0.5963 - val_loss: 0.7205 - val_accuracy: 0.6735
Epoch 5/20
10/10 [==============================] - 1s 66ms/step - loss: 0.6527 - accuracy: 0.6371 - val_loss: 0.7812 - val_accuracy: 0.6599
Epoch 6/20
10/10 [==============================] - 1s 66ms/step - loss: 0.6885 - accuracy: 0.6235 - val_loss: 0.9922 - val_accuracy: 0.6463
Epoch 7/20
10/10 [==============================] - 1s 65ms/step - loss: 0.7068 - accuracy: 0.6252 - val_loss: 0.7086 - val_accuracy: 0.6803
Epoch 8/20
1

In [30]:
model.save('cnn+lstm.h5')  

/opt/conda/lib/python3.10/site-packages/keras/src/engine/training.py:3000: UserWarning: You are saving your model as an HDF5 file via `model.save()`. This file format is considered legacy. We recommend using instead the native Keras format, e.g. `model.save('my_model.keras')`.
  saving_api.save_model(


In [ ]:
app = Flask(__name__)


model = load_model('/kaggle/working/cnn+lstm.h5')


@app.route('/predict', methods=['POST'])
def predict():
    try:
  
        file = request.files['/kaggle/input/medical-image-dataset-brain-tumor-detection/TumorDetectionYolov8/OD8/Brain Tumor Detection/test/images/volume_100_slice_105_jpg.rf.cdacd3f7e2631df9516f8f0283ac430c.jpg']
        
        
        img = image.load_img(file, target_size=(224, 224))
        img_array = image.img_to_array(img)
        img_array = np.expand_dims(img_array, axis=0)
        img_array /= 255.0  # Normalize pixel values to [0, 1]

      
        predictions = model.predict(img_array)
        predicted_class = np.argmax(predictions)

       
        response = {
            'class': int(predicted_class),
            'confidence': float(predictions[0][predicted_class])
        }
        return jsonify(response)

    except Exception as e:
        return jsonify({'error': str(e)}), 500

if __name__ == '__main__':
    app.run(port=5000, debug=False)

 * Serving Flask app '__main__'
 * Debug mode: off
